In [2]:
!pip install pyLDAvis

In [59]:
import pandas as pd
import numpy as np

# NLTK
from nltk.tokenize import RegexpTokenizer
from nltk.stem import PorterStemmer
from nltk.corpus import stopwords
import re

# Visualization
import matplotlib.pyplot as plt
import matplotlib.patches as mpatches
import matplotlib
%matplotlib inline
import seaborn as sns

# Model 1: Data Science Job Post

In [60]:
job_1 = 'Masters Degree in Operations Research, Applied Statistics, Data Mining, Machine Learning or a related quantitative \
discipline.Highly skilled at R Python programming for data science. Deep understanding of statistical and machine-learning \
approaches, including supervised (regression and classification techniques) and unsupervised (clustering) learning, as well as \
recommendation methods. Use of graphical packages, like ggplot2, matplotlib, plotly, or seaborn, to visualize outcomes to a wide \
audience. 4-5+ years’ experience delivering world-class data science outcomes, you solve complex analytical problems using quantitative \
approaches with your unique blend of analytical, mathematical and technical skills.Excellent communication skills, not only with \
other analytically-minded individuals, but a wider audience.Experience with cloud computing environments and \
tooling (e.g. AWS, Azure, Domino Data Lab). Familiarity with the software development lifecycle. Ability to independently navigate \
the data science process, ranging from identifying a business problem, acquiring data, experimenting with solutions, and sharing \
results. Familiarity and background in health care data analytics and use of protected health care data.'

job_2 = 'In pursuit of an undergraduate, graduate, or PhD degree at a four-year institution in Data Science, Math, Physics, Statistics,\
Computer Science,  Engineering, or related field.Deep desire to manipulate and analyze complex, high-volume, highly dimensional\
data from varying sources.Passion for empirical research and answering hard questions with data and models.Knowledge of statistical\
concepts such as correlation, linear regression, optimization, and how they can be applied.Exposure to statistical analysis\
tools/frameworks such as NumPy/SciPy/Pandas/SciKit learn, or SparkML.Expertise in Machine Learning/Cognitive Computing algorithms \
and techniques would be a bonus.Excellent problem solver with the ability to take initiative.Able to present findings and communicate \
effectively.Able to work collaboratively across teams and leverage constructive feedback.Naturally curious and skeptical.'

job_3 = 'Experience in data mining, data analysis, and predictive modelingPrevious work experience in business intelligence and \
data analytics Proven experience utilizing statistical techniques to identify key insights from data to solve business Problems'

job_4 = 'Work with a team of data scientists, machine learning engineers, software engineers and QA engineers.Perform data \
collection, preprocessing, feature engineering, data visualization and analysis.Build automation of data collection and \
preprocessing.Build models to address business problems.Engage with lines of business, users and analysts to explore and \
prototype opportunities and use-cases exploiting data and the application of cognitive and machine learning technologies.\
Design, develop, test and support Cognitive microservices to operationalize and productize deployment of resulting models and \
cognitive solutions.Modern, object-oriented or functional programming experience, (Java, C++, Python, Scala, SQL, R)\
Data Science and Machine Learning Frameworks (R, Apache Spark / MLlib, TensorFlow, Scikit-learn, etc…)Natural Language \
Processing (NLTK, CoreNLP, Gensim, Spacy, etc..)Experience with Big-Data technologies and cloud (AWS, other)Linux / Bash scripting\
Relational databases (Oracle, PostgreSQL, MySQL, etc.)Agile development methodologyCI/CD Development environments \
and tools (GIT, Maven, Jenkins, etc)RESTful Microservice APIsStrong analytical skills. Previous experience or education \
focused on statistics or data science is valuable.Bachelors degree in Computer Science or related degree.At least 1 year of \
experience through internships or field related work experience.Experience in working on an Open Source project a plus but \
not required.Good English language skillsAppreciate the value of diversity (in all its forms) brings to our team and companyPh.D. \
or M.S. in Computer Science, Statistics, or related field.Proficient with at least one major programming language (Java, Scala, \
C++, Python).Experience with supervised and unsupervised machine learning algorithms.Strong grasp of data structures and algorithms.\
Good communication skills with both technical and business people. Ability to speak at a level appropriate for the audience.Cares\
deeply about agile software practices, data driven development, and collaborating with other researchers and engineers.'

job_5 = 'Design and implement data analysis, data mining, research, analysis, modeling strategies and best practices Use analytical\
expertise to spot key business insights, trends, and opportunities in our vast database Help interpret and communicate your findings\
in a way that is easily understood by those less familiar with data Collaborate with a dynamic Product and Development team in delivering\
data products and insights to clients Establish and maintain relationships with distributed cross-functional teams to leverage domain and \
industry expertise Identify missing and inaccurate data in our platforms; seek out supplements and replacements to improve our data sets\
to the greatest extent possible Advise teams and clients as a subject matter expert in data science Bachelor’s degree in a quantitative\
field such as Statistics, Computer Science, Economics, or Mathematics; or equivalent work experience Relevant, successful professional \
industry experience Proficiency with database and analysis tools like R, SQL, Python, and others Expertise in statistical modeling, data\
collection, aggregation, analysis, machine learning, and productization Self-driven passion for finding and collaboratively solving \
problems Strong understanding of the benefits and flaws in the application of various methods'

job_6 = 'Bachelors or graduate degree in statistics/computer science or related field plus a minimum of 3 years applied analytics \
experience End-to-end experience developing approach/methodology given business need, ETL, data quality analysis, model development  \
and validation (machine learning or statistical), scoring, presentation of results and deployment into production environment\
(including AWS, Azure, Google Cloud) Strong experience with predictive models and clustering (segmentation) Strong/Expert SQL, \
Python, R, in a Hadoop environment H2O experience a plus Experience with Tableau, Birst, Microsoft Excel and PowerPoint Travel\
Requirement may be required, up to 20% Strong team player, flexible, and creative Experience with marketing related analytics\
channels/metrics, especially digital Passion/Curiosity around new techniques, ie deep learning Identity resolution experience, \
data with multiple levels and sources – aggregating & connecting Ability to learn and lead with minimal oversight, work on several \
projects at same time Strong communication and presentation skills, ability to maintain timeline'

## Step 1: Preprocess our text.

In [61]:
def text_process(text):
    '''
    Takes in a string of text, then performs the following:
        1. Tokenizes and removes punctuation
        2. Removes stopwords
        3. Stems
        4. Returns a list of the cleaned text
    '''
    if pd.isnull(text):
        return []
    # tokenizing and removing punctuation
    tokenizer = RegexpTokenizer(r'\w+')
    text_processed=tokenizer.tokenize(text)
    
    # removing any stopwords
    text_processed = [word.lower() for word in text_processed if word.lower() not in stopwords.words('english')]
    
    # steming (commented out to get the non stemmed words)
#     porter_stemmer = PorterStemmer()
    
#     text_processed = [porter_stemmer.stem(word) for word in text_processed]
    
    try:
        text_processed.remove('b')
    except: 
        pass

    return text_processed ## <-- one small tweak

In [62]:
texts = [text_process(job_1),
         text_process(job_2),
         text_process(job_3),
         text_process(job_4),
         text_process(job_5),
        text_process(job_6)]

## Step 2: Fit LDA Model.

In [63]:
from gensim import corpora, models
# from scipy.special.logsumexp import 
import pyLDAvis.gensim

In [64]:
pyLDAvis.enable_notebook()

In [65]:
np.random.seed(42) # want to have reproducable resuslts

In [66]:
dictionary = corpora.Dictionary(texts)

corpus = [dictionary.doc2bow(text) for text in texts] # bow = bag of words


# Instantiate the model
ldamodel = models.ldamodel.LdaModel(corpus=corpus,
                                   id2word=dictionary,
                                    num_topics=4,
                                   passes=50, # similar to epochs in neural networks
                                   minimum_probability=0)

/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

...

/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



## Step 3: Visualize LDA model.

In [67]:
pyLDAvis.gensim.prepare(ldamodel, corpus, dictionary)

/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/pyLDAvis/_prepare.py:387: DeprecationWarning: 
.ix is deprecated. Please use
.loc for label based indexing or
.iloc for positional indexing

See the documentation here:
http://pandas.pydata.org/pandas-docs/stable/indexing.html#ix-indexer-is-deprecated
  topic_term_dists = topic_term_dists.ix[topic_order]


PreparedData(topic_coordinates=            Freq  cluster  topics         x         y
topic                                                
1      60.132268        1       1 -0.087103 -0.013396
2      39.431688        1       2  0.096774 -0.010846
3       0.218022        1       3 -0.004836  0.012120
0       0.218022        1       4 -0.004836  0.012121, topic_info=     Category       Freq             Term      Total  loglift  logprob
term                                                                  
6     Default  24.000000             data  24.000000  30.0000  30.0000
125   Default   3.000000           models   3.000000  29.0000  29.0000
111   Default   3.000000            field   3.000000  28.0000  28.0000
141   Default   3.000000        cognitive   3.000000  27.0000  27.0000
216   Default   3.000000              etc   3.000000  26.0000  26.0000
174   Default   3.000000        engineers   3.000000  25.0000  25.0000
10    Default   5.000000          related   5.000000  24.0000  24.0000
163   Default   5.000000         analysis   5.000000  23.0000  23.0000
138   Default   2.000000            learn   2.000000  22.0000  22.0000
254   Default   2.000000             plus   2.000000  21.0000  21.0000
142   Default   2.000000       algorithms   2.000000  20.0000  20.0000
218   Default   2.000000         language   2.000000  19.0000  19.0000
267   Default   5.000000           strong   5.000000  18.0000  18.0000
82    Default   4.000000          ability   4.000000  17.0000  17.0000
109   Default   4.000000         computer   4.000000  16.0000  16.0000
171   Default   2.000000         insights   2.000000  15.0000  15.0000
7     Default   2.000000           mining   2.000000  14.0000  14.0000
55    Default   3.000000         problems   3.000000  13.0000  13.0000
33    Default   3.000000              use   3.000000  12.0000  12.0000
172   Default   3.000000             team   3.000000  11.0000  11.0000
21    Default   4.000000      statistical   4.000000  10.0000  10.0000
88    Default   6.000000         business   6.000000   9.0000   9.0000
153   Default   5.000000             work   5.000000   8.0000   8.0000
5     Default   5.000000       statistics   5.000000   7.0000   7.0000
1     Default   5.000000           degree   5.000000   6.0000   6.0000
80    Default   5.000000      development   5.000000   5.0000   5.0000
148   Default   1.000000             able   1.000000   4.0000   4.0000
102   Default   1.000000         graduate   1.000000   3.0000   3.0000
119   Default   1.000000          sources   1.000000   2.0000   2.0000
358   Default   1.000000      environment   1.000000   1.0000   1.0000
...       ...        ...              ...        ...      ...      ...
46     Topic4   0.003749                5   1.117891   0.4307  -5.9814
57     Topic4   0.003749           unique   1.117891   0.4307  -5.9814
56     Topic4   0.003749            using   1.117891   0.4307  -5.9814
38     Topic4   0.003749       matplotlib   1.117891   0.4307  -5.9814
164    Topic4   0.003750       predictive   1.920797  -0.1104  -5.9813
27     Topic4   0.003750       techniques   3.451492  -0.6966  -5.9813
98     Topic4   0.003750        analytics   2.648523  -0.4318  -5.9813
153    Topic4   0.003750             work   5.057456  -1.0786  -5.9813
21     Topic4   0.003750      statistical   4.179203  -0.8879  -5.9813
48     Topic4   0.003750       experience  16.725758  -2.2747  -5.9813
88     Topic4   0.003750         business   6.512909  -1.3316  -5.9813
6      Topic4   0.003750             data  24.730628  -2.6658  -5.9814
69     Topic4   0.003750        computing   1.920800  -0.1105  -5.9814
53     Topic4   0.003750          complex   1.920800  -0.1105  -5.9814
62     Topic4   0.003750        excellent   1.920800  -0.1105  -5.9814
89     Topic4   0.003750          problem   1.920800  -0.1105  -5.9814
25     Topic4   0.003750       regression   1.920800  -0.1105  -5.9814
13     Topic4   0.003750           highly   1.920801  -0.1105  -5.9814
154    Topic

## Step 4: Update model with new data!

In [68]:
job_7 = 'PhD degree in computer science, or related technical, math, or scientific field Strong working knowledge of \
deep learning, machine learning and statistics. Hands on experience building models with deep learning frameworks like \
MXNet, Tensorflow, Caffe, Torch, Theano or similar. Experience in using Python, R or Matlab or other statistical/machine \
learning software Strong communication and data presentation skills The motivation to achieve results in a fast-paced \
environment. Experience with statistical modeling / machine learning Strong attention to detail Comfortable working in a \
fast paced, highly collaborative, dynamic work environment Ability to think creatively and solve problems'

In [69]:
new_doc = text_process(job_7)

In [70]:
ldamodel.update([dictionary.doc2bow(new_doc)])

/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

In [71]:
job_8 = 'ability to tell meaningful stories with data. Programming skills in Python Experience with SQL, database modeling and \
data warehousing principles. Creativity to go beyond current tools to deliver best solution to the problem. Data visualization \
experience in Matplotlib, Tableau, ggplot2 or a similar tool. Experience with data science algorithms including decision trees, \
probability networks, association rules, clustering, regression, and neural networks. Excellent interpersonal, written, and verbal \
communication skills. Ability and comfort working independently and making key decisions on projects. Build and monitor effective \
reporting and alerting for fraud and operational health of a line of business.  Perform ad-hoc and re-occurring statistical and data \
science analyses.  Work closely with data warehouse architects and software developers to generate seamless business intelligence \
solutions for end users.  Support production analytic solutions.  Present results of analyses to business units.'

In [72]:
new_doc2 = text_process(job_8)

In [73]:
ldamodel.update([dictionary.doc2bow(new_doc2)])

/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

In [74]:
job_9 = 'Work in a collaborative, fast-paced environment with a team of smart, passionate developers, product managers, and designers\
 Rapidly iterate on a search and analytics SaaS product with a quickly growing number of users Own features and functionality \
 from design through deployment Design and develop algorithms, models, and pipelines that power the analytics of earned \
 media based on Machine Learning and Natural Language Processing (NLP) techniques Gain insights using data science techniques, \
 implement models, and engineer services to exploit those insights Practical experience at large scale in one or more of \
 the following domains: natural language processing, machine learning, search, information retrieval or text classification \
 Solid experience in Java, Python, Scala, or another object-oriented language Familiarity with ML/NLP frameworks such as \
 scikit-learn, Weka, Pandas, Mallet, TensorFlow, PyTorch, Theano Ability to thrive in a fast-paced, unstructured and dynamic \
 environment US Citizen or Permanent Resident (We will not sponsor at this time) Good understanding of system design, distributed \
 systems, cloud infrastructure, service-oriented solutions, scalable web services Familiarity with using clustered computing \
 systems, such as Hadoop/MapReduce, Spark/SparkR, Lucene/ElasticSearch, Storm, etc Familiarity with Agile development methodologies \
 (Kanban preferred)'

In [75]:
new_doc3 = text_process(job_9)

In [76]:
ldamodel.update([dictionary.doc2bow(new_doc3)])

/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

In [77]:
job_10 = 'Use data science and machine learning to drive product innovation, customer success, marketing optimization, and more\
Help champion a data-driven culture and push long-term business value creation through development of best-in-class data science \
capabilities Leverage data science, computer vision, and machine learning to increase value across our businesses Train computer \
vision and deep learning models on the big data resources Optimize computer vision algorithms and deep learning models to run \
efficiently in production system Work with engineers from prototype to production Minimum of M.S. in Computer Science, Math, Physics, \
Engineering, Statistics or other technical fields. 2+ years working experience in machine learning / computer vision / deep learning. \
Expert level in machine learning, computer vision, and deep learning. Proven track record of completing multiple data science projects \
end to end, from idea generation to objectives formulation to implementation and deliverables. Proficiency in C/C++, Java, SQL, Python, \
and multi-threaded programming. Experience with Hadoop stack (HIVE, Pig, Hadoop streaming), MapReduce and SPARK. Experience with deep \
learning tools (tensorFlow, caffe(2)).  Excellent written and oral communication skills Highly skilled at translating business \
requirements from key stakeholders into shovel-ready work plans Excellent project management skills, with a proven track record of \
on-time and within-budget delivery'

In [78]:
new_doc4 = text_process(job_10)

In [79]:
ldamodel.update([dictionary.doc2bow(new_doc4)])

/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/gensim/models/ldamodel.py:776: DeprecationWarning: `logsumexp` is deprecated!
Importing `logsumexp` from scipy.misc is deprecated in scipy 1.0.0. Use `scipy.special.logsumexp` instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

In [80]:
pyLDAvis.gensim.prepare(ldamodel, corpus, dictionary)

/Users/guillermogonzalez/miniconda3/envs/ga/lib/python3.6/site-packages/pyLDAvis/_prepare.py:387: DeprecationWarning: 
.ix is deprecated. Please use
.loc for label based indexing or
.iloc for positional indexing

See the documentation here:
http://pandas.pydata.org/pandas-docs/stable/indexing.html#ix-indexer-is-deprecated
  topic_term_dists = topic_term_dists.ix[topic_order]


PreparedData(topic_coordinates=            Freq  cluster  topics         x         y
topic                                                
2      32.436922        1       1 -0.011438  0.123673
0      31.968385        1       2 -0.011442  0.123669
3      19.943835        1       3  0.250241 -0.111822
1      15.650858        1       4 -0.227360 -0.135520, topic_info=     Category       Freq           Term      Total  loglift  logprob
term                                                                
9     Default  26.000000       learning  26.000000  30.0000  30.0000
8     Default  12.000000        machine  12.000000  29.0000  29.0000
109   Default  10.000000       computer  10.000000  28.0000  28.0000
18    Default  14.000000        science  14.000000  27.0000  27.0000
6     Default  15.000000           data  15.000000  26.0000  26.0000
19    Default   8.000000           deep   8.000000  25.0000  25.0000
48    Default   9.000000     experience   9.000000  24.0000  24.0000
125   Default   6.000000         models   6.000000  23.0000  23.0000
361   Default   6.000000         hadoop   6.000000  22.0000  22.0000
153   Default   6.000000           work   6.000000  21.0000  21.0000
61    Default   4.000000         skills   4.000000  20.0000  20.0000
88    Default   4.000000       business   4.000000  19.0000  19.0000
345   Default   4.000000            end   4.000000  18.0000  18.0000
357   Default   4.000000     production   4.000000  17.0000  17.0000
62    Default   4.000000      excellent   4.000000  16.0000  16.0000
259   Default   4.000000          value   4.000000  15.0000  15.0000
209   Default   4.000000              c   4.000000  14.0000  14.0000
167   Default   4.000000         proven   4.000000  13.0000  13.0000
298   Default   4.000000        product   4.000000  12.0000  12.0000
142   Default   4.000000     algorithms   4.000000  11.0000  11.0000
213   Default   4.000000          spark   4.000000  10.0000  10.0000
394   Default   4.000000           time   4.000000   9.0000   9.0000
208   Default   4.000000           java   4.000000   8.0000   8.0000
80    Default   4.000000    development   4.000000   7.0000   7.0000
215   Default   4.000000     tensorflow   4.000000   6.0000   6.0000
16    Default   4.000000         python   4.000000   5.0000   5.0000
250   Default   2.000000        working   2.000000   4.0000   4.0000
63    Default   2.000000  communication   2.000000   3.0000   3.0000
211   Default   2.000000            sql   2.000000   2.0000   2.0000
17    Default   2.000000    programming   2.000000   1.0000   1.0000
...       ...        ...            ...        ...      ...      ...
211    Topic4   1.526669            sql   2.710124   1.2807  -4.2458
393    Topic4   1.526669       projects   2.710124   1.2807  -4.2458
235    Topic4   1.526669          tools   2.710124   1.2807  -4.2458
282    Topic4   1.526669           best   2.710124   1.2807  -4.2458
170    Topic4   1.526669            key   2.710124   1.2807  -4.2458
107    Topic4   1.526668           math   2.710124   1.2807  -4.2458
13     Topic4   1.526668         highly   2.710124   1.2807  -4.2458
5      Topic4   1.526668     statistics   2.710124   1.2807  -4.2458
60     Topic4   1.526668      technical   2.710124   1.2807  -4.2458
174    Topic4   1.526668      engineers   2.710124   1.2807  -4.2458
110    Topic4   1.526668    engineering   2.710124   1.2807  -4.2458
130    Topic4   1.526668   optimization   2.710124   1.2807  -4.2458
51     Topic4   1.526668          class   2.710124   1.2807  -4.2458
343    Topic4   1.526668        minimum   2.710124   1.2807  -4.2458
276    Topic4   1.526668         driven   2.710124   1.2807  -4.2458
332    Topic4   1.526668    proficiency   2.710124   1.2807  -4.2458
272    Topic4   1.526668          level   2.710124   1.2807  -4.2458
385    Topic4   1.526668       multiple   2.710124   1.2807  -4.2458
14     Topic4   1.526668        skilled   2.710124   1.2807  -4.2458
374    Topic4   1.526668      marketing   2.7

In [85]:
# TOPIC 1
ldamodel.print_topics(num_topics=4)

[(0,
  '0.003*"computer" + 0.003*"deep" + 0.003*"business" + 0.003*"excellent" + 0.003*"production" + 0.003*"end" + 0.003*"proven" + 0.003*"c" + 0.003*"value" + 0.003*"skills"'),
 (1,
  '0.084*"computer" + 0.070*"deep" + 0.028*"skills" + 0.028*"business" + 0.028*"end" + 0.028*"production" + 0.028*"excellent" + 0.028*"proven" + 0.028*"value" + 0.028*"c"'),
 (2,
  '0.003*"computer" + 0.003*"deep" + 0.003*"c" + 0.003*"proven" + 0.003*"value" + 0.003*"excellent" + 0.003*"production" + 0.003*"end" + 0.003*"business" + 0.003*"skills"'),
 (3,
  '0.186*"learning" + 0.089*"science" + 0.087*"data" + 0.083*"machine" + 0.062*"experience" + 0.042*"models" + 0.042*"hadoop" + 0.042*"work" + 0.021*"product" + 0.021*"algorithms"')]